In [1]:
import pandas as pd 

In [2]:
df = pd.read_excel('/home/limeng/SICT/lung_test/数据采集接口规范（喉癌）.xlsx')
df

节点名    表名     节点类型   宽度 是否必传      注释             说明
0         COC_HBZL_RYJL$kh  入院记录       字符   32    Y      卡号        患者就诊卡卡号
1        COC_HBZL_RYJL$klx  入院记录       字符   16    Y     卡类型          参见字典表
2       COC_HBZL_RYJL$xgbz  入院记录       字符    1    Y    修改标志  1:正常 2:修改3:撤销
3      COC_HBZL_RYJL$yjlxh  入院记录       字符   32    Y   原纪录序号         院内唯一标识
4       COC_HBZL_RYJL$hzbh  入院记录  varchar   64    Y    患者编号            NaN
...                    ...   ...      ...  ...  ...     ...            ...
1137   COC_HBZL_SFJL$hgnpg  随访记录  varchar  500  NaN   喉功能评估            NaN
1138  COC_HBZL_SFJL$zhzlsj  随访记录  varchar   20  NaN  综合治疗时间       【天/月/年】后
1139  COC_HBZL_SFJL$zhzlfa  随访记录  varchar  500  NaN  综合治疗方案            NaN
1140     COC_HBZL_SFJL$sxz  随访记录  varchar   50  NaN     书写者            NaN
1141    COC_HBZL_SFJL$cjsj  随访记录  varchar   20  NaN    创建时间            NaN

[1142 rows x 7 columns]

In [3]:
df.to_csv('regular.csv',index = False)

In [12]:
import pandas as pd
import difflib

def get_best_match(target, choices):
    """使用difflib找到最佳匹配"""
    matches = difflib.get_close_matches(target, choices, n=1, cutoff=0.6)
    return matches[0] if matches else None

# 读取规范文件
regular_df = pd.read_csv('/home/limeng/SICT/lung_test/regular.csv')

# 读取测试数据
test_df = pd.read_csv('/home/limeng/SICT/lung_test/喉癌患者测试样例.csv', encoding='ISO-8859-1')

# 创建规范字典，键为注释，值为对应的规则
regular_dict = dict(zip(regular_df['注释'], regular_df.to_dict('records')))

# 创建新的注释列
matched_annotations = []
for _, row in test_df.iterrows():
    # 组合三个字段
    combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
    
    # 在规范中查找最佳匹配
    best_match = get_best_match(combined_field, regular_dict.keys())
    matched_annotations.append(best_match if best_match else "未匹配")

# 获取ValueItemKind列的位置
kind_idx = test_df.columns.get_loc('ValueItemKind')

# 在ValueItemKind列前插入新的注释列
test_df.insert(kind_idx, 'Matched_Annotation', matched_annotations)

# 保存结果
test_df.to_csv('/home/limeng/SICT/lung_test/喉癌患者测试样例_with_annotations.csv', index=False)

# 打印匹配结果统计
print("\n匹配结果统计:")
print(pd.Series(matched_annotations).value_counts())


匹配结果统计:
未匹配    127
Name: count, dtype: int64


In [15]:
import pandas as pd
import difflib
import chardet

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    def get_best_match(target, choices):
        """使用difflib找到最佳匹配"""
        matches = difflib.get_close_matches(target, choices, n=1, cutoff=0.6)
        return matches[0] if matches else None

    # 创建规范字典，键为注释，值为对应的规则
    regular_dict = dict(zip(regular_df['注释'], regular_df.to_dict('records')))

    # 创建新的注释列
    matched_annotations = []
    for _, row in test_df.iterrows():
        # 组合三个字段
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        
        # 在规范中查找最佳匹配
        best_match = get_best_match(combined_field, regular_dict.keys())
        matched_annotations.append(best_match if best_match else "未匹配")

    # 获取ValueItemKind列的位置
    kind_idx = test_df.columns.get_loc('ValueItemKind')

    # 在ValueItemKind列前插入新的注释列
    test_df.insert(kind_idx, 'Matched_Annotation', matched_annotations)

    # 保存结果
    test_df.to_csv('/home/limeng/SICT/lung_test/喉癌患者测试样例_with_annotations.csv', 
                   index=False, encoding=test_encoding)

    # 打印匹配结果统计
    print("\n匹配结果统计:")
    print(pd.Series(matched_annotations).value_counts())
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！

匹配结果统计:
未匹配          123
现病史-精神状态       1
体格检查-精神状态      1
体格检查-呼吸        1
体格检查-查体        1
Name: count, dtype: int64


In [19]:
import pandas as pd
import numpy as np
from sentence_transformers import SentenceTransformer
import chardet

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 加载预训练的中文Sentence Transformer模型
    print("加载Sentence Transformer模型...")
    model = SentenceTransformer('/home/limeng/SICT/lung_test/all-MiniLM-L6-v2')  # 多语言模型，支持中文
    
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 计算规范注释的嵌入向量
    print("计算规范注释的嵌入向量...")
    regular_embeddings = model.encode(regular_annotations, show_progress_bar=True)
    
    # 创建新的注释列
    matched_annotations = []
    matched_scores = []
    
    print("开始匹配注释...")
    # 批量处理测试数据中的字段组合
    combined_fields = []
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 计算测试数据的嵌入向量
    test_embeddings = model.encode(combined_fields, show_progress_bar=True)
    
    # 计算相似度并找到最佳匹配
    for i, test_embedding in enumerate(test_embeddings):
        # 计算与所有规范注释的余弦相似度
        similarities = np.dot(regular_embeddings, test_embedding) / (
            np.linalg.norm(regular_embeddings, axis=1) * np.linalg.norm(test_embedding)
        )
        
        # 找到最佳匹配
        best_match_idx = np.argmax(similarities)
        best_match_score = similarities[best_match_idx]
        
        # 如果相似度低于阈值，标记为未匹配
        if best_match_score < 0.5:  # 可以调整这个阈值
            matched_annotations.append("未匹配")
            matched_scores.append(0.0)
        else:
            matched_annotations.append(regular_annotations[best_match_idx])
            matched_scores.append(best_match_score)
    
    # 获取ValueItemKind列的位置
    kind_idx = test_df.columns.get_loc('ValueItemKind')
    
    # 在ValueItemKind列前插入新的注释列和相似度分数列
    test_df.insert(kind_idx, 'Matched_Score', matched_scores)
    test_df.insert(kind_idx, 'Matched_Annotation', matched_annotations)
    
    # 保存结果
    test_df.to_csv('/home/limeng/SICT/lung_test/喉癌患者测试样例_with_annotations_transformer.csv', 
                   index=False, encoding=test_encoding)
    
    # 打印匹配结果统计
    print("\n匹配结果统计:")
    print(pd.Series(matched_annotations).value_counts())
    
    # 打印前5行匹配结果示例
    print("\n前5行匹配结果示例:")
    for i in range(min(5, len(test_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"匹配注释: {test_df.iloc[i]['Matched_Annotation']}")
        print(f"相似度分数: {test_df.iloc[i]['Matched_Score']:.4f}")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
加载Sentence Transformer模型...
计算规范注释的嵌入向量...


Batches: 100%|██████████| 36/36 [00:01<00:00, 24.81it/s]


开始匹配注释...


Batches: 100%|██████████| 4/4 [00:00<00:00, 113.98it/s]



匹配结果统计:
未匹配                    14
手术类型                   10
皮肤黏膜-皮下出血               9
辅助检查-乙肝病毒-医院名称          9
患者基本情况                  5
主任医师签名日期                5
手术医师签名                  5
下一步治疗方案-具体方案            5
发起科室参与人员-主任医师           5
一般情况-主要症状及体征-姓名         5
一般情况-发育                 3
中断放疗-是否                 3
个人史-疫源接触史-接触时间          3
甲状腺-左侧甲状腺包块-有无          3
第一助手                    2
第二助手                    2
出院时情况                   2
以下血管结构可见肿瘤包饶-颈总动脉       2
现病史-精神状态                2
入院时情况-主诉                2
病理报告-检查日期               2
入院时情况-患者年龄              2
讨论经过-病理科-医师姓名           2
系统回顾-运动骨骼系统-关节肿痛-时长     2
辅助检查-心电图-检查结论           2
颈部-颈部气管切开-硅胶气管筒         2
既往史-过敏史-药物食物过敏源         1
一般情况-神志                 1
现病史-大便                  1
系统回顾-泌尿系统-排尿困难          1
系统回顾-神经精神系统-癫痫          1
脊柱四肢-关节活动               1
咽-喉咽-喉咽后壁新生物-形态         1
讨论经过-病理科-病理结果           1
环后区-其他描述                1
系统回顾-泌尿系统-排尿困难-服用药物     1
系统回顾-血液系统-鼻衄史-目前清理      1
记录医师签名日期                1
一般情

In [2]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba
import Levenshtein
from fuzzywuzzy import fuzz

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 定义多种相似度计算方法
    def calculate_similarities(query, candidates):
        """计算多种相似度指标"""
        results = []
        
        # 1. TF-IDF + 余弦相似度
        try:
            # 对中文文本进行分词
            segmented_query = ' '.join(jieba.cut(query))
            segmented_candidates = [' '.join(jieba.cut(c)) for c in candidates]
            
            # 计算TF-IDF向量
            vectorizer = TfidfVectorizer()
            tfidf_matrix = vectorizer.fit_transform([segmented_query] + segmented_candidates)
            
            # 计算余弦相似度
            cosine_sim = cosine_similarity(tfidf_matrix[0:1], tfidf_matrix[1:]).flatten()
            
            # 找到最佳匹配
            best_idx_tfidf = np.argmax(cosine_sim)
            best_score_tfidf = cosine_sim[best_idx_tfidf]
            results.append((candidates[best_idx_tfidf], best_score_tfidf, "TF-IDF"))
        except Exception as e:
            print(f"TF-IDF计算失败: {e}")
        
        # 2. Levenshtein距离（编辑距离）
        try:
            lev_distances = [Levenshtein.distance(query, c) for c in candidates]
            # 将距离转换为相似度分数（越小越相似）
            max_len = max(len(query), max(len(c) for c in candidates))
            lev_similarities = [1 - dist/max_len for dist in lev_distances]
            
            best_idx_lev = np.argmax(lev_similarities)
            best_score_lev = lev_similarities[best_idx_lev]
            results.append((candidates[best_idx_lev], best_score_lev, "Levenshtein"))
        except Exception as e:
            print(f"Levenshtein计算失败: {e}")
        
        # 3. FuzzyWuzzy比率
        try:
            fuzzy_ratios = [fuzz.ratio(query, c)/100 for c in candidates]
            best_idx_fuzzy = np.argmax(fuzzy_ratios)
            best_score_fuzzy = fuzzy_ratios[best_idx_fuzzy]
            results.append((candidates[best_idx_fuzzy], best_score_fuzzy, "FuzzyWuzzy"))
        except Exception as e:
            print(f"FuzzyWuzzy计算失败: {e}")
        
        # 4. FuzzyWuzzy部分比率（处理子字符串）
        try:
            partial_ratios = [fuzz.partial_ratio(query, c)/100 for c in candidates]
            best_idx_partial = np.argmax(partial_ratios)
            best_score_partial = partial_ratios[best_idx_partial]
            results.append((candidates[best_idx_partial], best_score_partial, "Partial"))
        except Exception as e:
            print(f"Partial比率计算失败: {e}")
        
        # 5. FuzzyWuzzy令牌排序比率（处理词序不同）
        try:
            token_sort_ratios = [fuzz.token_sort_ratio(query, c)/100 for c in candidates]
            best_idx_token = np.argmax(token_sort_ratios)
            best_score_token = token_sort_ratios[best_idx_token]
            results.append((candidates[best_idx_token], best_score_token, "TokenSort"))
        except Exception as e:
            print(f"TokenSort比率计算失败: {e}")
        
        # 找出所有方法中得分最高的结果
        best_result = max(results, key=lambda x: x[1]) if results else (None, 0, None)
        
        return best_result
    
    # 对每个测试字段进行匹配
    matched_annotations = []
    matched_scores = []
    matched_methods = []
    
    print("开始匹配注释...")
    for i, query in enumerate(combined_fields):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(combined_fields)} 条记录...")
        
        # 计算多种相似度并选择最佳匹配
        best_match, best_score, best_method = calculate_similarities(query, regular_annotations)
        
        # 如果相似度低于阈值，标记为未匹配
        if best_score < 0.6:  # 可以调整这个阈值
            matched_annotations.append("未匹配")
            matched_scores.append(0.0)
            matched_methods.append("None")
        else:
            matched_annotations.append(best_match)
            matched_scores.append(best_score)
            matched_methods.append(best_method)
    
    # 获取ValueItemKind列的位置
    kind_idx = test_df.columns.get_loc('ValueItemKind')
    
    # 在ValueItemKind列前插入新的列
    test_df.insert(kind_idx, 'Matched_Method', matched_methods)
    test_df.insert(kind_idx, 'Matched_Score', matched_scores)
    test_df.insert(kind_idx, 'Matched_Annotation', matched_annotations)
    
    # 保存结果
    test_df.to_csv('/home/limeng/SICT/lung_test/喉癌患者测试样例_with_annotations_multi.csv', 
                   index=False, encoding=test_encoding)
    
    # 打印匹配结果统计
    print("\n匹配结果统计:")
    print(pd.Series(matched_annotations).value_counts().head(10))
    
    # 打印方法使用统计
    print("\n匹配方法使用统计:")
    print(pd.Series(matched_methods).value_counts())
    
    # 打印前5行匹配结果示例
    print("\n前5行匹配结果示例:")
    for i in range(min(5, len(test_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"匹配注释: {test_df.iloc[i]['Matched_Annotation']}")
        print(f"相似度分数: {test_df.iloc[i]['Matched_Score']:.4f}")
        print(f"匹配方法: {test_df.iloc[i]['Matched_Method']}")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

Building prefix dict from the default dictionary ...


测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
开始匹配注释...
处理第 0/127 条记录...


Dumping model to file cache /tmp/jieba.cache
Loading model cost 0.792 seconds.
Prefix dict has been built successfully.


处理第 100/127 条记录...

匹配结果统计:
体格检查    20
未匹配     20
手术经过    13
姓名      11
主刀医师    10
现病史      7
性别       5
手术名称     5
小结时间     5
麻醉方式     5
Name: count, dtype: int64

匹配方法使用统计:
Partial        100
None            20
Levenshtein      5
TF-IDF           2
Name: count, dtype: int64

前5行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
匹配注释: 姓名
相似度分数: 1.0000
匹配方法: Partial
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
匹配注释: 姓名
相似度分数: 1.0000
匹配方法: Partial
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
匹配注释: 姓名
相似度分数: 1.0000
匹配方法: Partial
--------------------------------------------------
原始字段: 病例特点-主诉-主诉
匹配注释: 主诉
相似度分数: 1.0000
匹配方法: Partial
--------------------------------------------------
原始字段: 病例特点-入院日期-入院日期
匹配注释: 病理报告-检查日期
相似度分数: 0.6774
匹配方法: Levenshtein
--------------------------------------------------


In [3]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba
import Levenshtein
from fuzzywuzzy import fuzz

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 定义多种相似度计算方法
    def calculate_similarities(query, candidates):
        """计算多种相似度指标，返回每种方法的最佳匹配"""
        results = {}
        
        # 1. TF-IDF + 余弦相似度
        try:
            # 对中文文本进行分词
            segmented_query = ' '.join(jieba.cut(query))
            segmented_candidates = [' '.join(jieba.cut(c)) for c in candidates]
            
            # 计算TF-IDF向量
            vectorizer = TfidfVectorizer()
            tfidf_matrix = vectorizer.fit_transform([segmented_query] + segmented_candidates)
            
            # 计算余弦相似度
            cosine_sim = cosine_similarity(tfidf_matrix[0:1], tfidf_matrix[1:]).flatten()
            
            # 找到最佳匹配
            best_idx_tfidf = np.argmax(cosine_sim)
            results['TF-IDF'] = candidates[best_idx_tfidf]
        except Exception as e:
            print(f"TF-IDF计算失败: {e}")
            results['TF-IDF'] = "未匹配"
        
        # 2. Levenshtein距离（编辑距离）
        try:
            lev_distances = [Levenshtein.distance(query, c) for c in candidates]
            # 将距离转换为相似度分数（越小越相似）
            best_idx_lev = np.argmin(lev_distances)
            results['Levenshtein'] = candidates[best_idx_lev]
        except Exception as e:
            print(f"Levenshtein计算失败: {e}")
            results['Levenshtein'] = "未匹配"
        
        # 3. FuzzyWuzzy比率
        try:
            fuzzy_ratios = [fuzz.ratio(query, c) for c in candidates]
            best_idx_fuzzy = np.argmax(fuzzy_ratios)
            results['FuzzyWuzzy'] = candidates[best_idx_fuzzy]
        except Exception as e:
            print(f"FuzzyWuzzy计算失败: {e}")
            results['FuzzyWuzzy'] = "未匹配"
        
        # 4. FuzzyWuzzy部分比率（处理子字符串）
        try:
            partial_ratios = [fuzz.partial_ratio(query, c) for c in candidates]
            best_idx_partial = np.argmax(partial_ratios)
            results['Partial'] = candidates[best_idx_partial]
        except Exception as e:
            print(f"Partial比率计算失败: {e}")
            results['Partial'] = "未匹配"
        
        # 5. FuzzyWuzzy令牌排序比率（处理词序不同）
        try:
            token_sort_ratios = [fuzz.token_sort_ratio(query, c) for c in candidates]
            best_idx_token = np.argmax(token_sort_ratios)
            results['TokenSort'] = candidates[best_idx_token]
        except Exception as e:
            print(f"TokenSort比率计算失败: {e}")
            results['TokenSort'] = "未匹配"
        
        return results
    
    # 对每个测试字段进行匹配
    tfidf_matches = []
    levenshtein_matches = []
    fuzzywuzzy_matches = []
    
    print("开始匹配注释...")
    for i, query in enumerate(combined_fields):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(combined_fields)} 条记录...")
        
        # 计算多种相似度
        matches = calculate_similarities(query, regular_annotations)
        
        # 保存各种方法的匹配结果
        tfidf_matches.append(matches.get('TF-IDF', "未匹配"))
        levenshtein_matches.append(matches.get('Levenshtein', "未匹配"))
        fuzzywuzzy_matches.append(matches.get('FuzzyWuzzy', "未匹配"))
    
    # 获取ValueItemKind列的位置
    kind_idx = test_df.columns.get_loc('ValueItemKind')
    
    # 在ValueItemKind列前插入新的列
    test_df.insert(kind_idx, 'FuzzyWuzzy_Match', fuzzywuzzy_matches)
    test_df.insert(kind_idx, 'Levenshtein_Match', levenshtein_matches)
    test_df.insert(kind_idx, 'TFIDF_Match', tfidf_matches)
    
    # 保存结果
    test_df.to_csv('/home/limeng/SICT/lung_test/喉癌患者测试样例_with_annotations_all.csv', 
                   index=False, encoding=test_encoding)
    
    # 打印匹配结果统计
    print("\n各方法匹配结果统计:")
    print("TF-IDF匹配结果:")
    print(pd.Series(tfidf_matches).value_counts().head(10))
    print("\nLevenshtein匹配结果:")
    print(pd.Series(levenshtein_matches).value_counts().head(10))
    print("\nFuzzyWuzzy匹配结果:")
    print(pd.Series(fuzzywuzzy_matches).value_counts().head(10))
    
    # 打印前5行匹配结果示例
    print("\n前5行匹配结果示例:")
    for i in range(min(5, len(test_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"TF-IDF匹配: {test_df.iloc[i]['TFIDF_Match']}")
        print(f"Levenshtein匹配: {test_df.iloc[i]['Levenshtein_Match']}")
        print(f"FuzzyWuzzy匹配: {test_df.iloc[i]['FuzzyWuzzy_Match']}")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
开始匹配注释...
处理第 0/127 条记录...
处理第 100/127 条记录...

各方法匹配结果统计:
TF-IDF匹配结果:
主刀医师                  15
卡号                    14
手术经过                  13
既往史-手术外伤史-手术史-手术时间    10
患者姓名                   7
患者基本情况                 6
手术名称                   5
麻醉方式                   5
参与人员                   4
主诉                     3
Name: count, dtype: int64

Levenshtein匹配结果:
既往史-手术外伤史-手术史-有无      13
体格检查-血压-收缩压           10
既往史-手术外伤史-手术史-手术时间    10
入院时情况-患者姓名             8
主要辅助检查-实验室检查-Na        8
主治医师签名                 6
既往史-手术外伤史-手术史-手术名称     5
患者性别                   5
主治医师签名时间               5
个人史-饮酒史-主要饮酒种类         5
Name: count, dtype: int64

FuzzyWuzzy匹配结果:
讨论经过-耳鼻喉科/眼科-具体手术方案    13
患者姓名                   11
既往史-手术外伤史-手术史-手术时间     10
体格检查-血压-收缩压             9
主要辅助检查-实验室检查-Na         8
主治医师签名                  6
发起科室参与人员-主任医师           5
麻醉方式                    5
患者性别                    5
既往史-手术外伤史-手术史-手术名称      5
Name: count, dtype: int64

前5行匹配结果示例:
原始字段: 病例

In [1]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba
import Levenshtein
from fuzzywuzzy import fuzz

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    paragraph_names = []
    statement_names = []
    value_item_names = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
        paragraph_names.append(row['ParagraphName'])
        statement_names.append(row['StatementName'])
        value_item_names.append(row['ValueItemName'])
    
    # 定义多种相似度计算方法
    def calculate_similarities(query, candidates):
        """计算多种相似度指标，返回每种方法的最佳匹配和分数"""
        results = {}
        scores = {}
        
        # 1. TF-IDF + 余弦相似度
        try:
            # 对中文文本进行分词
            segmented_query = ' '.join(jieba.cut(query))
            segmented_candidates = [' '.join(jieba.cut(c)) for c in candidates]
            
            # 计算TF-IDF向量
            vectorizer = TfidfVectorizer()
            tfidf_matrix = vectorizer.fit_transform([segmented_query] + segmented_candidates)
            
            # 计算余弦相似度
            cosine_sim = cosine_similarity(tfidf_matrix[0:1], tfidf_matrix[1:]).flatten()
            
            # 找到最佳匹配
            best_idx_tfidf = np.argmax(cosine_sim)
            results['TF-IDF'] = candidates[best_idx_tfidf]
            scores['TF-IDF'] = cosine_sim[best_idx_tfidf]
        except Exception as e:
            print(f"TF-IDF计算失败: {e}")
            results['TF-IDF'] = "未匹配"
            scores['TF-IDF'] = 0.0
        
        # 2. Levenshtein距离（编辑距离）
        try:
            lev_distances = [Levenshtein.distance(query, c) for c in candidates]
            # 将距离转换为相似度分数（越小越相似）
            max_len = max(len(query), max(len(c) for c in candidates))
            lev_similarities = [1 - dist/max_len for dist in lev_distances]
            
            best_idx_lev = np.argmax(lev_similarities)
            results['Levenshtein'] = candidates[best_idx_lev]
            scores['Levenshtein'] = lev_similarities[best_idx_lev]
        except Exception as e:
            print(f"Levenshtein计算失败: {e}")
            results['Levenshtein'] = "未匹配"
            scores['Levenshtein'] = 0.0
        
        # 3. FuzzyWuzzy比率
        try:
            fuzzy_ratios = [fuzz.ratio(query, c)/100 for c in candidates]
            best_idx_fuzzy = np.argmax(fuzzy_ratios)
            results['FuzzyWuzzy'] = candidates[best_idx_fuzzy]
            scores['FuzzyWuzzy'] = fuzzy_ratios[best_idx_fuzzy]
        except Exception as e:
            print(f"FuzzyWuzzy计算失败: {e}")
            results['FuzzyWuzzy'] = "未匹配"
            scores['FuzzyWuzzy'] = 0.0
        
        return results, scores
    
    # 对每个测试字段进行匹配
    tfidf_matches = []
    levenshtein_matches = []
    fuzzywuzzy_matches = []
    best_matches = []
    best_match_methods = []
    
    print("开始匹配注释...")
    for i in range(len(combined_fields)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(combined_fields)} 条记录...")
        
        query = combined_fields[i]
        paragraph_name = paragraph_names[i]
        value_item_name = value_item_names[i]
        
        # 1. 首先检查是否有注释包含ParagraphName
        paragraph_matches = [ann for ann in regular_annotations if paragraph_name in ann]
        
        if paragraph_matches:
            # 2. 如果有包含ParagraphName的注释，再检查是否有同时包含ValueItemName的
            value_matches = [ann for ann in paragraph_matches if value_item_name in ann]
            if value_matches:
                # 找到同时包含ParagraphName和ValueItemName的注释
                best_match = value_matches[0]  # 取第一个匹配
                best_match_method = "精确匹配(段落+值)"
            else:
                # 只找到包含ParagraphName的注释
                best_match = paragraph_matches[0]  # 取第一个匹配
                best_match_method = "段落匹配"
        else:
            # 3. 如果没有包含ParagraphName的注释，直接使用相似度指标
            matches, scores = calculate_similarities(query, regular_annotations)
            
            # 选择得分最高的方法
            best_method = max(scores.items(), key=lambda x: x[1])[0]
            best_match = matches[best_method]
            best_match_method = f"相似度({best_method})"
        
        # 计算相似度匹配以便比较
        matches, _ = calculate_similarities(query, regular_annotations)
        tfidf_matches.append(matches.get('TF-IDF', "未匹配"))
        levenshtein_matches.append(matches.get('Levenshtein', "未匹配"))
        fuzzywuzzy_matches.append(matches.get('FuzzyWuzzy', "未匹配"))
        
        best_matches.append(best_match)
        best_match_methods.append(best_match_method)
    
    # 获取ValueItemKind列的位置
    kind_idx = test_df.columns.get_loc('ValueItemKind')
    
    # 在ValueItemKind列前插入新的列
    test_df.insert(kind_idx, 'Best_Match_Method', best_match_methods)
    test_df.insert(kind_idx, 'Best_Match', best_matches)
    test_df.insert(kind_idx, 'FuzzyWuzzy_Match', fuzzywuzzy_matches)
    test_df.insert(kind_idx, 'Levenshtein_Match', levenshtein_matches)
    test_df.insert(kind_idx, 'TFIDF_Match', tfidf_matches)
    
    # 保存结果
    test_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_with_annotations_all3.csv', 
                   index=False, encoding=test_encoding)
    
    # 打印匹配结果统计
    print("\n最佳匹配方法统计:")
    print(pd.Series(best_match_methods).value_counts())
    
    print("\n各方法匹配结果统计:")
    print("最佳匹配结果:")
    print(pd.Series(best_matches).value_counts().head(10))
    print("\nTF-IDF匹配结果:")
    print(pd.Series(tfidf_matches).value_counts().head(10))
    print("\nLevenshtein匹配结果:")
    print(pd.Series(levenshtein_matches).value_counts().head(10))
    print("\nFuzzyWuzzy匹配结果:")
    print(pd.Series(fuzzywuzzy_matches).value_counts().head(10))
    
    # 打印前5行匹配结果示例
    print("\n前5行匹配结果示例:")
    for i in range(min(5, len(test_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"最佳匹配: {test_df.iloc[i]['Best_Match']} (方法: {test_df.iloc[i]['Best_Match_Method']})")
        print(f"TF-IDF匹配: {test_df.iloc[i]['TFIDF_Match']}")
        print(f"Levenshtein匹配: {test_df.iloc[i]['Levenshtein_Match']}")
        print(f"FuzzyWuzzy匹配: {test_df.iloc[i]['FuzzyWuzzy_Match']}")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

FileNotFoundError: [Errno 2] No such file or directory: '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'

In [ ]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    paragraph_names = []
    statement_names = []
    value_item_names = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
        paragraph_names.append(row['ParagraphName'])
        statement_names.append(row['StatementName'])
        value_item_names.append(row['ValueItemName'])
    
    # 定义TF-IDF相似度计算方法
    def calculate_tfidf_similarity(query, candidates):
        """计算TF-IDF相似度，返回最佳匹配和分数"""
        try:
            # 对中文文本进行分词
            segmented_query = ' '.join(jieba.cut(query))
            segmented_candidates = [' '.join(jieba.cut(c)) for c in candidates]
            
            # 计算TF-IDF向量
            vectorizer = TfidfVectorizer()
            tfidf_matrix = vectorizer.fit_transform([segmented_query] + segmented_candidates)
            
            # 计算余弦相似度
            cosine_sim = cosine_similarity(tfidf_matrix[0:1], tfidf_matrix[1:]).flatten()
            
            # 找到最佳匹配
            best_idx = np.argmax(cosine_sim)
            return candidates[best_idx], cosine_sim[best_idx]
        except Exception as e:
            print(f"TF-IDF计算失败: {e}")
            return "未匹配", 0.0
    
    # 对每个测试字段进行匹配
    tfidf_matches = []
    best_matches = []
    best_match_methods = []
    similarity_scores = []
    
    print("开始匹配注释...")
    for i in range(len(combined_fields)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(combined_fields)} 条记录...")
        
        query = combined_fields[i]
        paragraph_name = paragraph_names[i]
        value_item_name = value_item_names[i]
        
        # 1. 首先检查是否有注释包含ParagraphName
        paragraph_matches = [ann for ann in regular_annotations if paragraph_name in ann]
        
        if paragraph_matches:
            # 2. 如果有包含ParagraphName的注释，再检查是否有同时包含ValueItemName的
            value_matches = [ann for ann in paragraph_matches if value_item_name in ann]
            if value_matches:
                # 找到同时包含ParagraphName和ValueItemName的注释
                best_match = value_matches[0]  # 取第一个匹配
                best_match_method = "精确匹配(段落+值)"
                similarity_score = 1.0  # 精确匹配给予最高分
            else:
                # 只找到包含ParagraphName的注释
                best_match = paragraph_matches[0]  # 取第一个匹配
                best_match_method = "段落匹配"
                similarity_score = 0.8  # 段落匹配给予较高分
        else:
            # 3. 如果没有包含ParagraphName的注释，使用TF-IDF相似度
            best_match, similarity_score = calculate_tfidf_similarity(query, regular_annotations)
            best_match_method = "TF-IDF相似度"
        
        # 计算TF-IDF匹配以便比较
        tfidf_match, _ = calculate_tfidf_similarity(query, regular_annotations)
        tfidf_matches.append(tfidf_match)
        
        best_matches.append(best_match)
        best_match_methods.append(best_match_method)
        similarity_scores.append(similarity_score)
    
    # 获取ValueItemKind列的位置
    kind_idx = test_df.columns.get_loc('ValueItemKind')
    
    # 在ValueItemKind列前插入新的列
    test_df.insert(kind_idx, 'Similarity_Score', similarity_scores)
    test_df.insert(kind_idx, 'Best_Match_Method', best_match_methods)
    test_df.insert(kind_idx, 'Best_Match', best_matches)
    test_df.insert(kind_idx, 'TFIDF_Match', tfidf_matches)
    
    # 保存结果
    test_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_with_tfidf.csv', 
                   index=False, encoding=test_encoding)
    
    # 打印匹配结果统计
    print("\n最佳匹配方法统计:")
    print(pd.Series(best_match_methods).value_counts())
    
    print("\n匹配结果统计:")
    print("最佳匹配结果:")
    print(pd.Series(best_matches).value_counts().head(10))
    print("\nTF-IDF匹配结果:")
    print(pd.Series(tfidf_matches).value_counts().head(10))
    
    # 打印前5行匹配结果示例
    print("\n前5行匹配结果示例:")
    for i in range(min(5, len(test_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"最佳匹配: {test_df.iloc[i]['Best_Match']} (方法: {test_df.iloc[i]['Best_Match_Method']})")
        print(f"相似度分数: {test_df.iloc[i]['Similarity_Score']:.4f}")
        print(f"TF-IDF匹配: {test_df.iloc[i]['TFIDF_Match']}")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache


测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
开始匹配注释...
处理第 0/127 条记录...


Loading model cost 1.175 seconds.
Prefix dict has been built successfully.


处理第 100/127 条记录...

最佳匹配方法统计:
TF-IDF相似度     89
段落匹配          32
精确匹配(段落+值)     6
Name: count, dtype: int64

匹配结果统计:
最佳匹配结果:
体格检查-体温               20
主刀医师                  15
卡号                    14
手术经过                  13
既往史-手术外伤史-手术史-手术时间    10
患者姓名                   7
患者基本情况                 6
现病史-发病日期               6
麻醉方式                   5
手术名称                   5
Name: count, dtype: int64

TF-IDF匹配结果:
主刀医师                  15
卡号                    14
手术经过                  13
既往史-手术外伤史-手术史-手术时间    10
患者姓名                   7
患者基本情况                 6
手术名称                   5
麻醉方式                   5
参与人员                   4
主诉                     3
Name: count, dtype: int64

前5行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
最佳匹配: 患者姓名 (方法: TF-IDF相似度)
相似度分数: 0.5819
TF-IDF匹配: 患者姓名
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
最佳匹配: 患者性别 (方法: TF-IDF相似度)
相似度分数: 0.6637
TF-IDF匹配: 患者性别
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
最佳匹配: 患者

In [7]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 定义TF-IDF相似度计算方法，返回前3个最佳匹配
    def calculate_top3_tfidf_similarity(query, candidates):
        """计算TF-IDF相似度，返回前3个最佳匹配和分数"""
        try:
            # 对中文文本进行分词
            segmented_query = ' '.join(jieba.cut(query))
            segmented_candidates = [' '.join(jieba.cut(c)) for c in candidates]
            
            # 计算TF-IDF向量
            vectorizer = TfidfVectorizer()
            tfidf_matrix = vectorizer.fit_transform([segmented_query] + segmented_candidates)
            
            # 计算余弦相似度
            cosine_sim = cosine_similarity(tfidf_matrix[0:1], tfidf_matrix[1:]).flatten()
            
            # 找到前3个最佳匹配
            top3_indices = np.argsort(cosine_sim)[::-1][:3]
            top3_scores = cosine_sim[top3_indices]
            
            return top3_indices, top3_scores
        except Exception as e:
            print(f"TF-IDF计算失败: {e}")
            return [-1, -1, -1], [0.0, 0.0, 0.0]
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用TF-IDF相似度匹配，获取前3个最佳匹配
        top3_indices, top3_scores = calculate_top3_tfidf_similarity(query, regular_annotations)
        
        # 获取测试数据的相关字段
        paragraph_name = test_df.iloc[i]['ParagraphName']
        statement_name = test_df.iloc[i]['StatementName']
        value_item_name = test_df.iloc[i]['ValueItemName']
        display_string = test_df.iloc[i]['DisplayString']
        
        # 获取前3个规范数据的相关字段
        regular_nodes = []
        regular_annotations_matched = []
        regular_descriptions = []
        
        for idx, score in zip(top3_indices, top3_scores):
            if idx >= 0:
                regular_nodes.append(regular_df.iloc[idx]['节点名'])
                regular_annotations_matched.append(regular_df.iloc[idx]['注释'])
                regular_descriptions.append(regular_df.iloc[idx]['说明'])
            else:
                regular_nodes.append("未匹配")
                regular_annotations_matched.append("未匹配")
                regular_descriptions.append("未匹配")
        
        # 确保有3个结果（如果候选项少于3个）
        while len(regular_nodes) < 3:
            regular_nodes.append("未匹配")
            regular_annotations_matched.append("未匹配")
            regular_descriptions.append("未匹配")
            top3_scores = np.append(top3_scores, 0.0)
        
        # 添加到结果数据
        result_data.append({
            'ParagraphName': paragraph_name,
            'StatementName': statement_name,
            'ValueItemName': value_item_name,
            'DisplayString': display_string,
            '规范节点名1': regular_nodes[0],
            '规范注释1': regular_annotations_matched[0],
            '规范说明1': regular_descriptions[0],
            '相似度分数1': top3_scores[0],
            '规范节点名2': regular_nodes[1],
            '规范注释2': regular_annotations_matched[1],
            '规范说明2': regular_descriptions[1],
            '相似度分数2': top3_scores[1],
            '规范节点名3': regular_nodes[2],
            '规范注释3': regular_annotations_matched[2],
            '规范说明3': regular_descriptions[2],
            '相似度分数3': top3_scores[2]
        })
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 保存结果
    result_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_top3_match.csv', 
                     index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_top3_match.csv")
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"匹配1: {result_df.iloc[i]['规范注释1']} (分数: {result_df.iloc[i]['相似度分数1']:.4f})")
        print(f"匹配2: {result_df.iloc[i]['规范注释2']} (分数: {result_df.iloc[i]['相似度分数2']:.4f})")
        print(f"匹配3: {result_df.iloc[i]['规范注释3']} (分数: {result_df.iloc[i]['相似度分数3']:.4f})")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
开始匹配注释...
处理第 0/127 条记录...
处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_top3_match.csv

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
匹配1: 患者姓名 (分数: 0.5819)
匹配2: 患者姓名 (分数: 0.5819)
匹配3: 姓名 (分数: 0.5574)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
匹配1: 患者性别 (分数: 0.6637)
匹配2: 性别 (分数: 0.6416)
匹配3: 性别 (分数: 0.6416)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
匹配1: 患者年龄 (分数: 0.6576)
匹配2: 年龄 (分数: 0.6348)
匹配3: 年龄 (分数: 0.6348)
--------------------------------------------------


In [9]:
import pandas as pd
import numpy as np
import chardet
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
import torch

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 加载预训练的中文Sentence Transformer模型
    print("加载Sentence Transformer模型...")
    
            # 如果都失败，尝试加载基础模型
    model = SentenceTransformer('/home/limeng/SICT/lung_test/all-MiniLM-L6-v2')

    # 定义Sentence Transformer相似度计算方法，返回前3个最佳匹配
    def calculate_top3_transformer_similarity(query, candidates, model):
        """计算Sentence Transformer相似度，返回前3个最佳匹配和分数"""
        try:
            # 编码查询和候选项
            query_embedding = model.encode([query], convert_to_tensor=True)
            candidate_embeddings = model.encode(candidates, convert_to_tensor=True)
            
            # 计算余弦相似度
            cosine_scores = cosine_similarity(
                query_embedding.cpu().numpy(), 
                candidate_embeddings.cpu().numpy()
            )[0]
            
            # 找到前3个最佳匹配
            top3_indices = np.argsort(cosine_scores)[::-1][:3]
            top3_scores = cosine_scores[top3_indices]
            
            return top3_indices, top3_scores
        except Exception as e:
            print(f"Transformer相似度计算失败: {e}")
            return [-1, -1, -1], [0.0, 0.0, 0.0]
    
    # 创建结果DataFrame
    result_data = []
    
    # 先对规范注释进行编码，避免重复计算
    print("对规范注释进行编码...")
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用Sentence Transformer相似度匹配，获取前3个最佳匹配
        top3_indices, top3_scores = calculate_top3_transformer_similarity(query, regular_annotations, model)
        
        # 获取测试数据的相关字段
        paragraph_name = test_df.iloc[i]['ParagraphName']
        statement_name = test_df.iloc[i]['StatementName']
        value_item_name = test_df.iloc[i]['ValueItemName']
        display_string = test_df.iloc[i]['DisplayString']
        
        # 获取前3个规范数据的相关字段
        regular_nodes = []
        regular_annotations_matched = []
        regular_descriptions = []
        
        for idx, score in zip(top3_indices, top3_scores):
            if idx >= 0:
                regular_nodes.append(regular_df.iloc[idx]['节点名'])
                regular_annotations_matched.append(regular_df.iloc[idx]['注释'])
                regular_descriptions.append(regular_df.iloc[idx]['说明'])
            else:
                regular_nodes.append("未匹配")
                regular_annotations_matched.append("未匹配")
                regular_descriptions.append("未匹配")
        
        # 确保有3个结果（如果候选项少于3个）
        while len(regular_nodes) < 3:
            regular_nodes.append("未匹配")
            regular_annotations_matched.append("未匹配")
            regular_descriptions.append("未匹配")
            top3_scores = np.append(top3_scores, 0.0)
        
        # 添加到结果数据
        result_data.append({
            'ParagraphName': paragraph_name,
            'StatementName': statement_name,
            'ValueItemName': value_item_name,
            'DisplayString': display_string,
            '规范节点名1': regular_nodes[0],
            '规范注释1': regular_annotations_matched[0],
            '规范说明1': regular_descriptions[0],
            '相似度分数1': top3_scores[0],
            '规范节点名2': regular_nodes[1],
            '规范注释2': regular_annotations_matched[1],
            '规范说明2': regular_descriptions[1],
            '相似度分数2': top3_scores[1],
            '规范节点名3': regular_nodes[2],
            '规范注释3': regular_annotations_matched[2],
            '规范说明3': regular_descriptions[2],
            '相似度分数3': top3_scores[2]
        })
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 保存结果
    result_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_transformer_top3_match.csv', 
                     index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_transformer_top3_match.csv")
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"匹配1: {result_df.iloc[i]['规范注释1']} (分数: {result_df.iloc[i]['相似度分数1']:.4f})")
        print(f"匹配2: {result_df.iloc[i]['规范注释2']} (分数: {result_df.iloc[i]['相似度分数2']:.4f})")
        print(f"匹配3: {result_df.iloc[i]['规范注释3']} (分数: {result_df.iloc[i]['相似度分数3']:.4f})")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
加载Sentence Transformer模型...
对规范注释进行编码...
开始匹配注释...
处理第 0/127 条记录...
处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_transformer_top3_match.csv

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
匹配1: 讨论经过-病理科-医师姓名 (分数: 0.8398)
匹配2: 讨论经过-放射科-医师姓名 (分数: 0.8398)
匹配3: 讨论经过-放化疗科-医师姓名 (分数: 0.8384)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
匹配1: 辅助检查-乙肝病毒-医院名称 (分数: 0.8360)
匹配2: 辅助检查-骨扫描检查-医院名称 (分数: 0.8325)
匹配3: 讨论经过-病理科-医师姓名 (分数: 0.8265)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
匹配1: 入院时情况-患者年龄 (分数: 0.8390)
匹配2: 辅助检查-乙肝病毒-医院名称 (分数: 0.8046)
匹配3: 辅助检查-骨扫描检查-医院名称 (分数: 0.8012)
--------------------------------------------------


In [1]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 使用TF-IDF向量化文本
    print("初始化TF-IDF向量化器...")
    
    # 对中文文本进行分词处理
    def tokenize_chinese(text):
        return list(jieba.cut(text))
    
    # 初始化TF-IDF向量化器
    tfidf_vectorizer = TfidfVectorizer(tokenizer=tokenize_chinese, analyzer='word')
    
    # 定义TF-IDF相似度计算方法，返回前3个最佳匹配
    def calculate_top3_tfidf_similarity(query, candidates, vectorizer):
        """计算TF-IDF相似度，返回前3个最佳匹配和分数"""
        try:
            # 将所有文本合并为一个列表进行向量化
            all_texts = [query] + candidates
            
            # 拟合并转换所有文本
            tfidf_matrix = vectorizer.fit_transform(all_texts)
            
            # 计算查询与所有候选项的余弦相似度
            query_vector = tfidf_matrix[0:1]
            candidate_vectors = tfidf_matrix[1:]
            
            cosine_scores = cosine_similarity(query_vector, candidate_vectors)[0]
            
            # 找到前3个最佳匹配
            top3_indices = np.argsort(cosine_scores)[::-1][:3]
            top3_scores = cosine_scores[top3_indices]
            
            return top3_indices, top3_scores
        except Exception as e:
            print(f"TF-IDF相似度计算失败: {e}")
            return [-1, -1, -1], [0.0, 0.0, 0.0]
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用TF-IDF相似度匹配，获取前3个最佳匹配
        top3_indices, top3_scores = calculate_top3_tfidf_similarity(query, regular_annotations, tfidf_vectorizer)
        
        # 获取测试数据的相关字段
        paragraph_name = test_df.iloc[i]['ParagraphName']
        statement_name = test_df.iloc[i]['StatementName']
        value_item_name = test_df.iloc[i]['ValueItemName']
        display_string = test_df.iloc[i]['DisplayString']
        
        # 获取前3个规范数据的相关字段
        regular_nodes = []
        regular_annotations_matched = []
        regular_descriptions = []
        
        for idx, score in zip(top3_indices, top3_scores):
            if idx >= 0:
                regular_nodes.append(regular_df.iloc[idx]['节点名'])
                regular_annotations_matched.append(regular_df.iloc[idx]['注释'])
                regular_descriptions.append(regular_df.iloc[idx]['说明'])
            else:
                regular_nodes.append("未匹配")
                regular_annotations_matched.append("未匹配")
                regular_descriptions.append("未匹配")
        
        # 确保有3个结果（如果候选项少于3个）
        while len(regular_nodes) < 3:
            regular_nodes.append("未匹配")
            regular_annotations_matched.append("未匹配")
            regular_descriptions.append("未匹配")
            top3_scores = np.append(top3_scores, 0.0)
        
        # 添加到结果数据
        result_data.append({
            'ParagraphName': paragraph_name,
            'StatementName': statement_name,
            'ValueItemName': value_item_name,
            'DisplayString': display_string,
            '规范节点名1': regular_nodes[0],
            '规范注释1': regular_annotations_matched[0],
            '规范说明1': regular_descriptions[0],
            '相似度分数1': top3_scores[0],
            '规范节点名2': regular_nodes[1],
            '规范注释2': regular_annotations_matched[1],
            '规范说明2': regular_descriptions[1],
            '相似度分数2': top3_scores[1],
            '规范节点名3': regular_nodes[2],
            '规范注释3': regular_annotations_matched[2],
            '规范说明3': regular_descriptions[2],
            '相似度分数3': top3_scores[2]
        })
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 保存结果
    result_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_top3_match.csv', 
                     index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_top3_match.csv")
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"匹配1: {result_df.iloc[i]['规范注释1']} (分数: {result_df.iloc[i]['相似度分数1']:.4f})")
        print(f"匹配2: {result_df.iloc[i]['规范注释2']} (分数: {result_df.iloc[i]['相似度分数2']:.4f})")
        print(f"匹配3: {result_df.iloc[i]['规范注释3']} (分数: {result_df.iloc[i]['相似度分数3']:.4f})")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
初始化TF-IDF向量化器...
开始匹配注释...
处理第 0/127 条记录...


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
Building prefix dict from the default dictionary ...
Dumping model to file cache /tmp/jieba.cache
Loading model cost 0.934 seconds.
Prefix dict has been built successfully.


处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_top3_match.csv

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
匹配1: 患者姓名 (分数: 0.4840)
匹配2: 患者姓名 (分数: 0.4840)
匹配3: 姓名 (分数: 0.4637)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
匹配1: 患者性别 (分数: 0.5414)
匹配2: 性别 (分数: 0.5235)
匹配3: 性别 (分数: 0.5235)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
匹配1: 患者年龄 (分数: 0.5357)
匹配2: 年龄 (分数: 0.5170)
匹配3: 年龄 (分数: 0.5170)
--------------------------------------------------


In [4]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 使用TF-IDF向量化文本
    print("初始化TF-IDF向量化器...")
    
    # 对中文文本进行分词处理
    def tokenize_chinese(text):
        return list(jieba.cut(text))
    
    # 初始化TF-IDF向量化器
    tfidf_vectorizer = TfidfVectorizer(tokenizer=tokenize_chinese, analyzer='word')
    
    # 定义TF-IDF相似度计算方法，返回最佳匹配（最多3个）
    def calculate_tfidf_similarity(query, candidates, vectorizer, max_matches=3, threshold=0.1):
        """计算TF-IDF相似度，返回最佳匹配（最多max_matches个）"""
        try:
            # 将所有文本合并为一个列表进行向量化
            all_texts = [query] + candidates
            
            # 拟合并转换所有文本
            tfidf_matrix = vectorizer.fit_transform(all_texts)
            
            # 计算查询与所有候选项的余弦相似度
            query_vector = tfidf_matrix[0:1]
            candidate_vectors = tfidf_matrix[1:]
            
            cosine_scores = cosine_similarity(query_vector, candidate_vectors)[0]
            
            # 找到相似度大于阈值的匹配
            valid_indices = np.where(cosine_scores > threshold)[0]
            
            # 按相似度降序排序
            sorted_indices = valid_indices[np.argsort(cosine_scores[valid_indices])[::-1]]
            
            # 最多取max_matches个
            top_indices = sorted_indices[:max_matches]
            top_scores = cosine_scores[top_indices]
            
            return top_indices, top_scores
        except Exception as e:
            print(f"TF-IDF相似度计算失败: {e}")
            return np.array([]), np.array([])
    
    # 定义FuzzyWuzzy相似度计算方法，返回最佳匹配（最多3个）
    def calculate_fuzzy_similarity(query, candidates, max_matches=3):
        """计算FuzzyWuzzy相似度，返回最佳匹配（最多max_matches个）"""
        try:
            # 使用process.extract获取最佳匹配
            matches = process.extract(query, candidates, limit=max_matches, scorer=fuzz.token_sort_ratio)
            
            # 提取索引和分数
            indices = []
            scores = []
            
            for match in matches:
                # match格式为(匹配文本, 分数)
                matched_text, score = match
                # 找到匹配文本在原始列表中的索引
                idx = candidates.index(matched_text)
                indices.append(idx)
                scores.append(score / 100.0)  # 将分数归一化到0-1范围
            
            return np.array(indices), np.array(scores)
        except Exception as e:
            print(f"FuzzyWuzzy相似度计算失败: {e}")
            return np.array([]), np.array([])
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用TF-IDF相似度匹配，获取最佳匹配（最多3个）
        tfidf_indices, tfidf_scores = calculate_tfidf_similarity(query, regular_annotations, tfidf_vectorizer)
        
        # 使用FuzzyWuzzy相似度匹配，获取最佳匹配（最多3个）
        fuzzy_indices, fuzzy_scores = calculate_fuzzy_similarity(query, regular_annotations)
        
        # 获取测试数据的相关字段
        paragraph_name = test_df.iloc[i]['ParagraphName']
        statement_name = test_df.iloc[i]['StatementName']
        value_item_name = test_df.iloc[i]['ValueItemName']
        display_string = test_df.iloc[i]['DisplayString']
        
        # 创建结果字典
        result_dict = {
            'ParagraphName': paragraph_name,
            'StatementName': statement_name,
            'ValueItemName': value_item_name,
            'DisplayString': display_string
        }
        
        # 添加TF-IDF匹配结果
        for j in range(min(3, len(tfidf_indices))):
            idx = tfidf_indices[j]
            score = tfidf_scores[j]
            result_dict[f'TFIDF_规范节点名{j+1}'] = regular_df.iloc[idx]['节点名']
            result_dict[f'TFIDF_规范注释{j+1}'] = regular_df.iloc[idx]['注释']
            result_dict[f'TFIDF_规范说明{j+1}'] = regular_df.iloc[idx]['说明']
            result_dict[f'TFIDF_相似度分数{j+1}'] = score
        
        # 添加FuzzyWuzzy匹配结果
        for j in range(min(3, len(fuzzy_indices))):
            idx = fuzzy_indices[j]
            score = fuzzy_scores[j]
            result_dict[f'Fuzzy_规范节点名{j+1}'] = regular_df.iloc[idx]['节点名']
            result_dict[f'Fuzzy_规范注释{j+1}'] = regular_df.iloc[idx]['注释']
            result_dict[f'Fuzzy_规范说明{j+1}'] = regular_df.iloc[idx]['说明']
            result_dict[f'Fuzzy_相似度分数{j+1}'] = score
        
        # 添加到结果数据
        result_data.append(result_dict)
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 保存结果
    result_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_fuzzy_match.csv', 
                     index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_fuzzy_match.csv")
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        
        print("TF-IDF匹配结果:")
        for j in range(1, 4):
            if f'TFIDF_规范注释{j}' in result_df.columns and not pd.isna(result_df.iloc[i].get(f'TFIDF_规范注释{j}', None)):
                print(f"  匹配{j}: {result_df.iloc[i][f'TFIDF_规范注释{j}']} (分数: {result_df.iloc[i][f'TFIDF_相似度分数{j}']:.4f})")
        
        print("FuzzyWuzzy匹配结果:")
        for j in range(1, 4):
            if f'Fuzzy_规范注释{j}' in result_df.columns and not pd.isna(result_df.iloc[i].get(f'Fuzzy_规范注释{j}', None)):
                print(f"  匹配{j}: {result_df.iloc[i][f'Fuzzy_规范注释{j}']} (分数: {result_df.iloc[i][f'Fuzzy_相似度分数{j}']:.4f})")
        
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
初始化TF-IDF向量化器...
开始匹配注释...
处理第 0/127 条记录...


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_fuzzy_match.csv

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
TF-IDF匹配结果:
  匹配1: 患者姓名 (分数: 0.4840)
  匹配2: 患者姓名 (分数: 0.4840)
  匹配3: 姓名 (分数: 0.4637)
FuzzyWuzzy匹配结果:
  匹配1: 患者姓名 (分数: 0.3300)
  匹配2: 入院时情况-患者姓名 (分数: 0.3300)
  匹配3: 患者姓名 (分数: 0.3300)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
TF-IDF匹配结果:
  匹配1: 患者性别 (分数: 0.5414)
  匹配2: 性别 (分数: 0.5235)
  匹配3: 性别 (分数: 0.5235)
FuzzyWuzzy匹配结果:
  匹配1: 患者姓名 (分数: 0.3600)
  匹配2: 入院时情况-患者姓名 (分数: 0.3600)
  匹配3: 患者姓名 (分数: 0.3600)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
TF-IDF匹配结果:
  匹配1: 患者年龄 (分数: 0.5357)
  匹配2: 年龄 (分数: 0.5170)
  匹配3: 年龄 (分数: 0.5170)
FuzzyWuzzy匹配结果:
  匹配1: 患者姓名 (分数: 0.3600)
  匹配2: 入院时情况-患者姓名 (分数: 0.3600)
  匹配3: 患者姓名 (分数: 0.3600)
--------------------------------------------------


In [1]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 使用TF-IDF向量化文本
    print("初始化TF-IDF向量化器...")
    
    # 对中文文本进行分词处理
    def tokenize_chinese(text):
        return list(jieba.cut(text))
    
    # 初始化TF-IDF向量化器
    tfidf_vectorizer = TfidfVectorizer(tokenizer=tokenize_chinese, analyzer='word')
    
    # 定义TF-IDF相似度计算方法，只返回最佳匹配（分数最高的）
    def calculate_best_tfidf_match(query, candidates, vectorizer):
        """计算TF-IDF相似度，只返回最佳匹配（分数最高的）"""
        try:
            # 将所有文本合并为一个列表进行向量化
            all_texts = [query] + candidates
            
            # 拟合并转换所有文本
            tfidf_matrix = vectorizer.fit_transform(all_texts)
            
            # 计算查询与所有候选项的余弦相似度
            query_vector = tfidf_matrix[0:1]
            candidate_vectors = tfidf_matrix[1:]
            
            cosine_scores = cosine_similarity(query_vector, candidate_vectors)[0]
            
            # 找到分数最高的匹配
            best_index = np.argmax(cosine_scores)
            best_score = cosine_scores[best_index]
            
            return best_index, best_score
        except Exception as e:
            print(f"TF-IDF相似度计算失败: {e}")
            return -1, 0.0
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用TF-IDF相似度匹配，只获取最佳匹配
        best_index, best_score = calculate_best_tfidf_match(query, regular_annotations, tfidf_vectorizer)
        
        # 获取测试数据的相关字段
        row = test_df.iloc[i]
        
        # 创建结果字典，包含原始字段
        result_dict = {
            'ParagraphName': row['ParagraphName'],
            'StatementName': row['StatementName'],
            'ValueItemName': row['ValueItemName'],
            'DisplayString': row['DisplayString']
        }
        
        # 添加SFZH, XGRQ, IPBLH字段（如果存在）
        if 'SFZH' in test_df.columns:
            result_dict['SFZH'] = row['SFZH']
        if 'XGRQ' in test_df.columns:
            result_dict['XGRQ'] = row['XGRQ']
        if 'IPBLH' in test_df.columns:
            result_dict['IPBLH'] = row['IPBLH']
        
        # 添加最佳TF-IDF匹配结果
        if best_index >= 0:
            result_dict['TFIDF_规范节点名'] = regular_df.iloc[best_index]['节点名']
            result_dict['TFIDF_规范注释'] = regular_df.iloc[best_index]['注释']
            result_dict['TFIDF_规范说明'] = regular_df.iloc[best_index]['说明']
            result_dict['TFIDF_相似度分数'] = best_score
        else:
            result_dict['TFIDF_规范节点名'] = ''
            result_dict['TFIDF_规范注释'] = ''
            result_dict['TFIDF_规范说明'] = ''
            result_dict['TFIDF_相似度分数'] = 0.0
        
        # 添加到结果数据
        result_data.append(result_dict)
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 保存结果
    result_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_best_match.csv', 
                     index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_best_match.csv")
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"最佳匹配: {result_df.iloc[i]['TFIDF_规范注释']} (分数: {result_df.iloc[i]['TFIDF_相似度分数']:.4f})")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
Building prefix dict from the default dictionary ...
Loading model from cache /tmp/jieba.cache


测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
初始化TF-IDF向量化器...
开始匹配注释...
处理第 0/127 条记录...


Loading model cost 0.942 seconds.
Prefix dict has been built successfully.


处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_best_match.csv

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
最佳匹配: 患者姓名 (分数: 0.4840)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
最佳匹配: 患者性别 (分数: 0.5414)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
最佳匹配: 患者年龄 (分数: 0.5357)
--------------------------------------------------


In [ ]:
import os
import json
# import time
os.environ["NCCL_P2P_DISABLE"] = "1"
import torch 
# import pynvml
from vllm import LLM, SamplingParams
import torch.distributed as dist
import re
torch.cuda.empty_cache()
os.environ["TRANSFORMERS_OFFLINE"] = "1"
os.environ["HF_DATASETS_OFFLINE"] = "1"
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"



# 加载量化模型
llm = LLM(model="/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8", dtype="half",gpu_memory_utilization=0.9)

# 
sampling_params = SamplingParams(temperature=0.1, top_p=0.3, max_tokens = 256)

# 推理示例


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2025-03-10 09:55:11,393	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 03-10 09:55:19 config.py:350] This model supports multiple tasks: {'generate', 'embedding'}. Defaulting to 'generate'.
WARNING 03-10 09:55:19 config.py:428] gptq quantization is not fully optimized yet. The speed can be slower than non-quantized models.
INFO 03-10 09:55:19 llm_engine.py:249] Initializing an LLM engine (v0.6.4.post1) with config: model='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', speculative_config=None, tokenizer='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=32768, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=gptq, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines

[W310 09:55:20.487166102 CUDAAllocatorConfig.h:28] Warning: expandable_segments not supported on this platform (function operator())
Loading safetensors checkpoint shards:   0% Completed | 0/5 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  20% Completed | 1/5 [00:00<00:03,  1.24it/s]
Loading safetensors checkpoint shards:  40% Completed | 2/5 [00:03<00:04,  1.64s/it]
Loading safetensors checkpoint shards:  60% Completed | 3/5 [00:05<00:03,  1.92s/it]
Loading safetensors checkpoint shards:  80% Completed | 4/5 [00:08<00:02,  2.25s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:10<00:00,  2.26s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:10<00:00,  2.06s/it]



INFO 03-10 09:55:32 model_runner.py:1077] Loading model weights took 15.5028 GB
INFO 03-10 09:55:42 worker.py:232] Memory profiling results: total_gpu_memory=31.73GiB initial_memory_usage=15.89GiB peak_torch_memory=19.42GiB memory_usage_post_profile=15.96GiB non_torch_memory=0.45GiB kv_cache_size=8.69GiB gpu_memory_utilization=0.90
INFO 03-10 09:55:43 gpu_executor.py:113] # GPU blocks: 2965, # CPU blocks: 1365
INFO 03-10 09:55:43 gpu_executor.py:117] Maximum concurrency for 32768 tokens per request: 1.45x
INFO 03-10 09:55:46 model_runner.py:1400] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 03-10 09:55:46 model_runner.py:1404] If out-of-memory error occurs during cudagraph capture, consider decreasing `gpu_memory_utilization` or switching to eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INF

In [ ]:
import os
import json
# import time
os.environ["NCCL_P2P_DISABLE"] = "1"
import torch 
# import pynvml
from vllm import LLM, SamplingParams
import torch.distributed as dist
import re
torch.cuda.empty_cache()
os.environ["TRANSFORMERS_OFFLINE"] = "1"
os.environ["HF_DATASETS_OFFLINE"] = "1"
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"



# 加载量化模型
llm = LLM(model="/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8", dtype="half",gpu_memory_utilization=0.9)

# 
sampling_params = SamplingParams(temperature=0.1, top_p=0.3, max_tokens = 256)

# 推理示例


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2025-03-10 09:55:11,393	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 03-10 09:55:19 config.py:350] This model supports multiple tasks: {'generate', 'embedding'}. Defaulting to 'generate'.
WARNING 03-10 09:55:19 config.py:428] gptq quantization is not fully optimized yet. The speed can be slower than non-quantized models.
INFO 03-10 09:55:19 llm_engine.py:249] Initializing an LLM engine (v0.6.4.post1) with config: model='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', speculative_config=None, tokenizer='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=32768, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=gptq, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines

[W310 09:55:20.487166102 CUDAAllocatorConfig.h:28] Warning: expandable_segments not supported on this platform (function operator())
Loading safetensors checkpoint shards:   0% Completed | 0/5 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  20% Completed | 1/5 [00:00<00:03,  1.24it/s]
Loading safetensors checkpoint shards:  40% Completed | 2/5 [00:03<00:04,  1.64s/it]
Loading safetensors checkpoint shards:  60% Completed | 3/5 [00:05<00:03,  1.92s/it]
Loading safetensors checkpoint shards:  80% Completed | 4/5 [00:08<00:02,  2.25s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:10<00:00,  2.26s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:10<00:00,  2.06s/it]



INFO 03-10 09:55:32 model_runner.py:1077] Loading model weights took 15.5028 GB
INFO 03-10 09:55:42 worker.py:232] Memory profiling results: total_gpu_memory=31.73GiB initial_memory_usage=15.89GiB peak_torch_memory=19.42GiB memory_usage_post_profile=15.96GiB non_torch_memory=0.45GiB kv_cache_size=8.69GiB gpu_memory_utilization=0.90
INFO 03-10 09:55:43 gpu_executor.py:113] # GPU blocks: 2965, # CPU blocks: 1365
INFO 03-10 09:55:43 gpu_executor.py:117] Maximum concurrency for 32768 tokens per request: 1.45x
INFO 03-10 09:55:46 model_runner.py:1400] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 03-10 09:55:46 model_runner.py:1404] If out-of-memory error occurs during cudagraph capture, consider decreasing `gpu_memory_utilization` or switching to eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INF

In [3]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 使用TF-IDF向量化文本
    print("初始化TF-IDF向量化器...")
    
    # 对中文文本进行分词处理
    def tokenize_chinese(text):
        return list(jieba.cut(text))
    
    # 初始化TF-IDF向量化器
    tfidf_vectorizer = TfidfVectorizer(tokenizer=tokenize_chinese, analyzer='word')
    
    # 定义TF-IDF相似度计算方法，只返回最佳匹配（分数最高的）
    def calculate_best_tfidf_match(query, candidates, vectorizer):
        """计算TF-IDF相似度，只返回最佳匹配（分数最高的）"""
        try:
            # 将所有文本合并为一个列表进行向量化
            all_texts = [query] + candidates
            
            # 拟合并转换所有文本
            tfidf_matrix = vectorizer.fit_transform(all_texts)
            
            # 计算查询与所有候选项的余弦相似度
            query_vector = tfidf_matrix[0:1]
            candidate_vectors = tfidf_matrix[1:]
            
            cosine_scores = cosine_similarity(query_vector, candidate_vectors)[0]
            
            # 找到分数最高的匹配
            best_index = np.argmax(cosine_scores)
            best_score = cosine_scores[best_index]
            
            return best_index, best_score
        except Exception as e:
            print(f"TF-IDF相似度计算失败: {e}")
            return -1, 0.0
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用TF-IDF相似度匹配，只获取最佳匹配
        best_index, best_score = calculate_best_tfidf_match(query, regular_annotations, tfidf_vectorizer)
        
        # 获取测试数据的相关字段
        row = test_df.iloc[i]
        
        # 创建结果字典，包含原始字段
        result_dict = {
            'ParagraphName': row['ParagraphName'],
            'StatementName': row['StatementName'],
            'ValueItemName': row['ValueItemName'],
            'DisplayString': row['DisplayString']
        }
        
        # 添加id字段（如果存在）
        if 'Id' in test_df.columns:
            result_dict['Id'] = row['Id']
        
        # 添加SFZH, XGRQ, IPBLH字段（如果存在）
        if 'SFZH' in test_df.columns:
            result_dict['SFZH'] = row['SFZH']
        if 'XGRQ' in test_df.columns:
            result_dict['XGRQ'] = row['XGRQ']
        if 'IPBLH' in test_df.columns:
            result_dict['IPBLH'] = row['IPBLH']
        
        # 添加最佳TF-IDF匹配结果
        if best_index >= 0:
            result_dict['TFIDF_规范节点名'] = regular_df.iloc[best_index]['节点名']
            result_dict['TFIDF_规范注释'] = regular_df.iloc[best_index]['注释']
            result_dict['TFIDF_规范说明'] = regular_df.iloc[best_index]['说明']
            result_dict['TFIDF_相似度分数'] = best_score
        else:
            result_dict['TFIDF_规范节点名'] = ''
            result_dict['TFIDF_规范注释'] = ''
            result_dict['TFIDF_规范说明'] = ''
            result_dict['TFIDF_相似度分数'] = 0.0
        
        # 添加到结果数据
        result_data.append(result_dict)
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 保存结果
    result_df.to_csv('/home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_best_match.csv', 
                     index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_best_match.csv")
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"最佳匹配: {result_df.iloc[i]['TFIDF_规范注释']} (分数: {result_df.iloc[i]['TFIDF_相似度分数']:.4f})")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！
初始化TF-IDF向量化器...
开始匹配注释...
处理第 0/127 条记录...


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_tfidf_best_match.csv

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
最佳匹配: 患者姓名 (分数: 0.4840)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
最佳匹配: 患者性别 (分数: 0.5414)
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
最佳匹配: 患者年龄 (分数: 0.5357)
--------------------------------------------------


In [3]:
import pandas as pd
import numpy as np
import chardet
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
import jieba

# 首先检测文件的实际编码
def detect_encoding(file_path):
    with open(file_path, 'rb') as f:
        result = chardet.detect(f.read())
    return result['encoding']

# 检测文件编码
test_file = '/home/limeng/SICT/lung_test/data/喉癌患者测试样例.csv'
regular_file = '/home/limeng/SICT/lung_test/data/regular.csv'

test_encoding = detect_encoding(test_file)
regular_encoding = detect_encoding(regular_file)

print(f"测试文件编码: {test_encoding}")
print(f"规范文件编码: {regular_encoding}")

# 尝试使用检测到的编码读取文件
try:
    # 读取规范文件
    regular_df = pd.read_csv(regular_file, encoding=regular_encoding)
    
    # 读取测试数据
    test_df = pd.read_csv(test_file, encoding=test_encoding)
    
    print("文件成功读取！")
except Exception as e:
    print(f"使用检测到的编码读取失败: {e}")
    
    # 尝试其他常见编码
    encodings = ['gbk', 'gb18030', 'latin1', 'cp936', 'big5']
    
    for enc in encodings:
        try:
            print(f"尝试使用 {enc} 编码读取测试文件...")
            test_df = pd.read_csv(test_file, encoding=enc)
            print(f"成功使用 {enc} 读取测试文件")
            
            print(f"尝试使用 {enc} 编码读取规范文件...")
            regular_df = pd.read_csv(regular_file, encoding=enc)
            print(f"成功使用 {enc} 读取规范文件")
            
            test_encoding = enc
            regular_encoding = enc
            break
        except Exception as e:
            print(f"使用 {enc} 读取失败: {e}")

# 如果成功读取文件，继续处理
if 'test_df' in locals() and 'regular_df' in locals():
    # 打印测试文件的列名，以供参考
    print("\n测试文件的列名:")
    print(test_df.columns.tolist())
    
    # 创建规范字典，键为注释，值为对应的规则
    regular_annotations = regular_df['注释'].tolist()
    
    # 准备测试数据中的字段组合
    combined_fields = []
    
    for _, row in test_df.iterrows():
        combined_field = f"{row['ParagraphName']}-{row['StatementName']}-{row['ValueItemName']}"
        combined_fields.append(combined_field)
    
    # 使用TF-IDF向量化文本
    print("\n初始化TF-IDF向量化器...")
    
    # 对中文文本进行分词处理
    def tokenize_chinese(text):
        return list(jieba.cut(text))
    
    # 初始化TF-IDF向量化器
    tfidf_vectorizer = TfidfVectorizer(tokenizer=tokenize_chinese, analyzer='word')
    
    # 定义TF-IDF相似度计算方法，只返回最佳匹配（分数最高的）
    def calculate_best_tfidf_match(query, candidates, vectorizer):
        """计算TF-IDF相似度，只返回最佳匹配（分数最高的）"""
        try:
            # 将所有文本合并为一个列表进行向量化
            all_texts = [query] + candidates
            
            # 拟合并转换所有文本
            tfidf_matrix = vectorizer.fit_transform(all_texts)
            
            # 计算查询与所有候选项的余弦相似度
            query_vector = tfidf_matrix[0:1]
            candidate_vectors = tfidf_matrix[1:]
            
            cosine_scores = cosine_similarity(query_vector, candidate_vectors)[0]
            
            # 找到分数最高的匹配
            best_index = np.argmax(cosine_scores)
            best_score = cosine_scores[best_index]
            
            return best_index, best_score
        except Exception as e:
            print(f"TF-IDF相似度计算失败: {e}")
            return -1, 0.0
    
    # 创建结果DataFrame
    result_data = []
    
    print("开始匹配注释...")
    
    for i in range(len(test_df)):
        if i % 100 == 0:
            print(f"处理第 {i}/{len(test_df)} 条记录...")
        
        query = combined_fields[i]
        
        # 使用TF-IDF相似度匹配，只获取最佳匹配
        best_index, best_score = calculate_best_tfidf_match(query, regular_annotations, tfidf_vectorizer)
        
        # 获取测试数据的行
        row = test_df.iloc[i]
        
        # 创建结果字典，包含测试数据的所有字段
        result_dict = row.to_dict()
        
        # 添加最佳TF-IDF匹配结果
        if best_index >= 0:
            result_dict['规范节点名'] = regular_df.iloc[best_index]['节点名']
            result_dict['规范注释'] = regular_df.iloc[best_index]['注释']
            result_dict['规范说明'] = regular_df.iloc[best_index]['说明']
            
            
            # 从最佳匹配中提取processed_string值
            # 如果需要对DisplayString进行处理，可以在此添加逻辑
            result_dict['processed_string'] = row['DisplayString']
        else:
            result_dict['规范节点名'] = ''
            result_dict['规范注释'] = ''
            result_dict['规范说明'] = ''
            
            result_dict['processed_string'] = ''
        
        # 添加到结果数据
        result_data.append(result_dict)
    
    # 创建结果DataFrame
    result_df = pd.DataFrame(result_data)
    
    # 重新排列列顺序，将匹配结果放在后面
    all_columns = test_df.columns.tolist() + ['规范节点名', '规范注释', '规范说明',  'processed_string']
    result_df = result_df[all_columns]
    
    # 保存结果
    result_file = '/home/limeng/SICT/lung_test/result/喉癌患者测试样例_完整字段_tfidf_match.csv'
    result_df.to_csv(result_file, index=False, encoding=test_encoding)
    
    print(f"\n匹配完成，共处理 {len(test_df)} 条记录")
    print(f"结果已保存至: {result_file}")
    
    # 打印结果DataFrame的列名
    print("\n结果文件的列名:")
    print(result_df.columns.tolist())
    
    # 打印前3行匹配结果示例
    print("\n前3行匹配结果示例:")
    for i in range(min(3, len(result_df))):
        print(f"原始字段: {combined_fields[i]}")
        print(f"最佳匹配: {result_df.iloc[i]['规范注释']}")
        print(f"处理后字符串: {result_df.iloc[i]['processed_string']}")
        print("-" * 50)
else:
    print("无法读取文件，请手动检查文件编码")

测试文件编码: GB2312
规范文件编码: utf-8
文件成功读取！

测试文件的列名:
['Id', 'PatientName', 'IPBLH', 'OPBLH', 'KH', 'KLX', 'SexId', 'CSRQ', 'ZJLX', 'SFZH', 'HYZK', 'ZYDM', 'GJDM', 'MZDM', 'JZDZ', 'YB', 'JG', 'HKDZ', 'DHHM', 'SJHM', 'ABOBloodTypeId', 'LXRXM', 'LXRGX', 'LXRDH', 'ZLLB', 'ZLMC', 'XGRQ', 'YJLXH', 'RYSJ', 'FolderName', 'Xh', 'RecordXh', 'FolderId', 'DocumentName', 'InstanceId', 'DocumentId', 'ParagraphId', 'ParagraphName', 'StatementId', 'StatementName', 'ValueId', 'ValueItemName', 'ValueItemKind', 'RealValue', 'ValueString', 'DisplayString', 'ValuePostfix', 'WSJLSCSJ', 'WSJLXGSJ', 'upload_time']

初始化TF-IDF向量化器...
开始匹配注释...
处理第 0/127 条记录...


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/sklearn/feature_extraction/text.py:517: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


处理第 100/127 条记录...

匹配完成，共处理 127 条记录
结果已保存至: /home/limeng/SICT/lung_test/result/喉癌患者测试样例_完整字段_tfidf_match.csv

结果文件的列名:
['Id', 'PatientName', 'IPBLH', 'OPBLH', 'KH', 'KLX', 'SexId', 'CSRQ', 'ZJLX', 'SFZH', 'HYZK', 'ZYDM', 'GJDM', 'MZDM', 'JZDZ', 'YB', 'JG', 'HKDZ', 'DHHM', 'SJHM', 'ABOBloodTypeId', 'LXRXM', 'LXRGX', 'LXRDH', 'ZLLB', 'ZLMC', 'XGRQ', 'YJLXH', 'RYSJ', 'FolderName', 'Xh', 'RecordXh', 'FolderId', 'DocumentName', 'InstanceId', 'DocumentId', 'ParagraphId', 'ParagraphName', 'StatementId', 'StatementName', 'ValueId', 'ValueItemName', 'ValueItemKind', 'RealValue', 'ValueString', 'DisplayString', 'ValuePostfix', 'WSJLSCSJ', 'WSJLXGSJ', 'upload_time', '规范节点名', '规范注释', '规范说明', 'processed_string']

前3行匹配结果示例:
原始字段: 病例特点-患者姓名、性别、年龄-病人姓名
最佳匹配: 患者姓名
处理后字符串: 测试
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-性别
最佳匹配: 患者性别
处理后字符串: 女
--------------------------------------------------
原始字段: 病例特点-患者姓名、性别、年龄-年龄
最佳匹配: 患者年龄
处理后字符串: 22岁
---------------------------------

In [ ]:
import os
import json
# import time
os.environ["NCCL_P2P_DISABLE"] = "1"
import torch 
# import pynvml
from vllm import LLM, SamplingParams
import torch.distributed as dist
import re
torch.cuda.empty_cache()
os.environ["TRANSFORMERS_OFFLINE"] = "1"
os.environ["HF_DATASETS_OFFLINE"] = "1"
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"



# 加载量化模型
llm = LLM(model="/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8", dtype="half",gpu_memory_utilization=0.9)

# 
sampling_params = SamplingParams(temperature=0.1, top_p=0.3, max_tokens = 256)

# 推理示例


/home/limeng/anaconda3/envs/Qwen2.5/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2025-03-10 09:55:11,393	INFO util.py:154 -- Missing packages: ['ipywidgets']. Run `pip install -U ipywidgets`, then restart the notebook server for rich notebook output.


INFO 03-10 09:55:19 config.py:350] This model supports multiple tasks: {'generate', 'embedding'}. Defaulting to 'generate'.
WARNING 03-10 09:55:19 config.py:428] gptq quantization is not fully optimized yet. The speed can be slower than non-quantized models.
INFO 03-10 09:55:19 llm_engine.py:249] Initializing an LLM engine (v0.6.4.post1) with config: model='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', speculative_config=None, tokenizer='/opt/lung/llm/Qwen/Qwen2.5-Coder-14B-Instruct-GPTQ-Int8', skip_tokenizer_init=False, tokenizer_mode=auto, revision=None, override_neuron_config=None, tokenizer_revision=None, trust_remote_code=False, dtype=torch.float16, max_seq_len=32768, download_dir=None, load_format=LoadFormat.AUTO, tensor_parallel_size=1, pipeline_parallel_size=1, disable_custom_all_reduce=False, quantization=gptq, enforce_eager=False, kv_cache_dtype=auto, quantization_param_path=None, device_config=cuda, decoding_config=DecodingConfig(guided_decoding_backend='outlines

[W310 09:55:20.487166102 CUDAAllocatorConfig.h:28] Warning: expandable_segments not supported on this platform (function operator())
Loading safetensors checkpoint shards:   0% Completed | 0/5 [00:00<?, ?it/s]
Loading safetensors checkpoint shards:  20% Completed | 1/5 [00:00<00:03,  1.24it/s]
Loading safetensors checkpoint shards:  40% Completed | 2/5 [00:03<00:04,  1.64s/it]
Loading safetensors checkpoint shards:  60% Completed | 3/5 [00:05<00:03,  1.92s/it]
Loading safetensors checkpoint shards:  80% Completed | 4/5 [00:08<00:02,  2.25s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:10<00:00,  2.26s/it]
Loading safetensors checkpoint shards: 100% Completed | 5/5 [00:10<00:00,  2.06s/it]



INFO 03-10 09:55:32 model_runner.py:1077] Loading model weights took 15.5028 GB
INFO 03-10 09:55:42 worker.py:232] Memory profiling results: total_gpu_memory=31.73GiB initial_memory_usage=15.89GiB peak_torch_memory=19.42GiB memory_usage_post_profile=15.96GiB non_torch_memory=0.45GiB kv_cache_size=8.69GiB gpu_memory_utilization=0.90
INFO 03-10 09:55:43 gpu_executor.py:113] # GPU blocks: 2965, # CPU blocks: 1365
INFO 03-10 09:55:43 gpu_executor.py:117] Maximum concurrency for 32768 tokens per request: 1.45x
INFO 03-10 09:55:46 model_runner.py:1400] Capturing cudagraphs for decoding. This may lead to unexpected consequences if the model is not static. To run the model in eager mode, set 'enforce_eager=True' or use '--enforce-eager' in the CLI.
INFO 03-10 09:55:46 model_runner.py:1404] If out-of-memory error occurs during cudagraph capture, consider decreasing `gpu_memory_utilization` or switching to eager mode. You can also reduce the `max_num_seqs` as needed to decrease memory usage.
INF